In [0]:
!pip install openpyxl

from pyspark.sql.functions import current_timestamp, current_date, concat, month, col, lit, when, round, floor, date_format, to_date, countDistinct, avg, sum, date_trunc, lag, min, array_contains, count
from pyspark.sql.types import LongType, DoubleType
from pyspark.sql.window import Window

import pandas as pd
import openpyxl
import itertools
import requests

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.9/250.9 kB 7.3 MB/s eta 0:00:00

[notice] A new release of pip available: 22.2.2 -> 25.3
[notice] To update, run: pip install --upgrade pip


In [0]:
pip install presto-python-client dotenv

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
import pandas as pd
import prestodb
import numpy as np
import datetime
from pyspark.sql import SparkSession

In [0]:
from dotenv import load_dotenv, find_dotenv
import os

# env_path = find_dotenv()

env_path = "/Workspace/Users/sheetal.suwalka@delhivery.com/.env"

print("Loading .env from:", env_path)
load_dotenv(dotenv_path=env_path, override=True)

Auth_token_key = os.getenv("Presto_query_authenticate_token")
user = os.getenv("user")
port = os.getenv("port")
host = os.getenv("host")

import prestodb

conn = prestodb.dbapi.connect(
        host=host,
        port=port,
        user = user,
        source='rstudio',
        catalog="awsdatacatalog",
        schema="express_dwh",
        http_scheme="http",
        http_headers = { "Authorization": f'''Bearer {Auth_token_key}'''})


Loading .env from: /Workspace/Users/sheetal.suwalka@delhivery.com/.env


In [0]:
# Create a SparkSession
spark = SparkSession.builder \
    .appName("example") \
    .config("spark.sql.parquet.mergeSchema", "true") \
    .getOrCreate() 

In [0]:
from datetime import datetime, timedelta

import pytz

# Define IST timezone
ist = pytz.timezone('Asia/Kolkata')

# Get current time in IST
current_time_ist = datetime.now(ist)
current_date = current_time_ist.strftime("%Y-%m-%d") 


print(current_date)

2025-11-27


In [0]:
from datetime import datetime, timedelta
import calendar
# from pyspark.sql.functions import  date_sub, expr, dayofweek


# Get the current date
today_date = datetime.now().date()
ad = today_date - timedelta(days = 20)
data_analysis_date = today_date - timedelta(days = 10)
print(ad, data_analysis_date)

2025-11-07 2025-11-17


In [0]:
# ad = '2025-11-10'
# trip_id  = 'trip-176358634779354166'

In [0]:
route_id_query = f'''
 select distinct route_schedule_uuid,  COALESCE(route_set_id, route_schedule_uuid) as route_set_id
from hudi_db.hudi_thanos_route_parquet 
-- where  route_set_id is not null
'''

In [0]:

cur = conn.cursor()
cur.execute(route_id_query)
columns = [desc[0] for desc in cur.description]
data = cur.fetchall()
route_id_route_set_mapping = pd.DataFrame(data, columns=columns)
cur.close()
conn.close()

In [0]:
route_id_route_set_mapping_spark  = spark.createDataFrame(route_id_route_set_mapping)

In [0]:
# display(route_id_route_set_mapping_spark.count())
# 1,296,763

2201187

In [0]:
# trips_arrive_depart_query = f'''
# select route_schedule_uuid, trip_uuid,route_type,  b.property_facility_name as center_name, 
# c.property_facility_name as next_center_name, scheduled_arrival_time, scheduled_depart_time,
# trip_arrival_time, last_shipment_load_time, trip_depart_time,
# mts_trip_depart_time
#  from (
# select *,  
# lead(scheduled_arrival_time,2) over(PARTITION by route_schedule_uuid, trip_uuid, action_center order by trip_arrival_time ) as scheduled_depart_time,
# lead(trip_arrival_time) over(PARTITION by route_schedule_uuid, trip_uuid, action_center order by trip_arrival_time ) as last_shipment_load_time ,
# lead(trip_arrival_time,2) over(PARTITION by route_schedule_uuid, trip_uuid, action_center order by trip_arrival_time ) as trip_depart_time,
# lead(trip_arrival_time,3) over(PARTITION by route_schedule_uuid, trip_uuid, action_center order by trip_arrival_time ) as mts_trip_depart_time

# from
# (
# ---- selecting arrival time
# (select route_schedule_uuid, trip_uuid,route_type, action_center, next_transit_center, action_performed, eta as scheduled_arrival_time, 
# min(trip_time) as trip_arrival_time
# from 
# (select distinct route_schedule_uuid,route_type,
# trip_uuid,
# action_entity,
# action_performed,
# action_center, next_transit_center,
# date(trip_creation_time + interval '330' minute) as trip_creation_time,
# (CAST(eta AS timestamp) + interval '330' minute) as eta,
# (CAST(etd AS timestamp) + interval '330' minute) as etd,
# from_unixtime( action_date/1000000.0) + interval '330' minute trip_time
# FROM express_dwh.trips_parquet
# where ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
#    and action_performed in ('Arrived')
#    -- and trip_uuid = '{trip_id}'
# order by trip_uuid,trip_time )
# group by 1,2,3,4,5,6,7)

# union 
# ---- selecting depart time
# (select route_schedule_uuid, trip_uuid,route_type, action_center, next_transit_center,action_performed, etd as scheduled_arrival_time,
#  max(trip_time) as trip_arrival_time
# from 
# (select distinct route_schedule_uuid,route_type,
# trip_uuid,
# action_entity,
# action_performed,
# action_center, next_transit_center,
# date(trip_creation_time + interval '330' minute) as trip_creation_time,
# (CAST(eta AS timestamp) + interval '330' minute) as eta,
# (CAST(etd AS timestamp) + interval '330' minute) as etd,
# from_unixtime( action_date/1000000.0) + interval '330' minute trip_time
# FROM express_dwh.trips_parquet
# where ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
#    and action_performed in ('Departed')
#    -- and trip_uuid = '{trip_id}'
# order by trip_uuid,trip_time )
# group by 1,2,3,4,5,6,7)

# union 
# ---- selecting MTS depart time
# (select route_schedule_uuid, trip_uuid,route_type, action_center, next_transit_center, action_performed,etd as scheduled_arrival_time, 
# max(trip_time) as trip_arrival_time
# from 
# (select distinct route_schedule_uuid,route_type,
# trip_uuid,
# action_entity,
# action_performed,
# action_center, next_transit_center,
# date(trip_creation_time + interval '330' minute) as trip_creation_time,
# (CAST(eta AS timestamp) + interval '330' minute) as eta,
# (CAST(etd AS timestamp) + interval '330' minute) as etd,
# from_unixtime( action_date/1000000.0) + interval '330' minute trip_time
# FROM express_dwh.trips_parquet
# where ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
#    and action_performed in ('Apply NSL') and nsl='DP-LF-01'
#    -- and trip_uuid = '{trip_id}'
# order by trip_uuid,trip_time )
# group by 1,2,3,4,5,6,7)

# union 
# ---- selecting Last shipment Load time
# (select route_schedule_uuid, trip_uuid,route_type, action_center, next_transit_center, action_performed,etd as scheduled_arrival_time, 
# max(trip_time) as trip_arrival_time
# from 
# (select distinct route_schedule_uuid,route_type,
# trip_uuid,
# action_entity,
# action_performed,
# action_center, next_transit_center,
# date(trip_creation_time + interval '330' minute) as trip_creation_time,
# (CAST(eta AS timestamp) + interval '330' minute) as eta,
# (CAST(etd AS timestamp) + interval '330' minute) as etd,
# from_unixtime( action_date/1000000.0) + interval '330' minute trip_time
# FROM express_dwh.trips_parquet
# where ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
#    and action_performed in ('Loading') 
#    -- and trip_uuid = '{trip_id}'
# order by trip_uuid,trip_time )
# group by 1,2,3,4,5,6,7)

# )
# ) a
# left join  hudi_db.hudi_facility_parquet b on a.action_center = b.property_facility_facility_code
# left join  hudi_db.hudi_facility_parquet c on a.next_transit_center = c.property_facility_facility_code

# where action_performed in ('Arrived')

# '''

In [0]:
trips_arrive_depart_query = f'''
WITH base_trips AS (
    SELECT 
        route_schedule_uuid,
        route_type,
        trip_uuid,
        action_center, position,
        next_transit_center,
        action_performed,
        vehicle_type, vehicle_type_sec, vehicle_number, vehicle_number_sec,
        nsl,
        (CAST(eta AS timestamp) + interval '330' minute) as eta,
        (CAST(etd AS timestamp) + interval '330' minute) as etd,
        (from_unixtime(action_date/1000000.0) + interval '330' minute) as trip_time,
        action_date
    FROM express_dwh.trips_parquet
    WHERE ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
  
      AND action_performed IN ('Arrived', 'Departed', 'Loading', 'Apply NSL','Completed')
       or  ((vehicle_number_sec is not null) and (trim(vehicle_number_sec) <> ''))  
),



arrival_info AS (
    SELECT 
        route_schedule_uuid, 
        trip_uuid,
        route_type, 
        action_center, position,
        next_transit_center, 
        eta as scheduled_arrival_time, 
        MIN(trip_time) as trip_arrival_time
    FROM base_trips
    WHERE action_performed = 'Arrived' and next_transit_center is not null
    GROUP BY 1,2,3,4,5,6,7
),


depart_info AS (
    SELECT 
        trip_uuid, 
        action_center,
        etd as scheduled_depart_time,
        MAX(trip_time) as trip_depart_time
    FROM base_trips
    WHERE action_performed = 'Departed' 
    GROUP BY 1,2,3
),

mts_info AS (
    SELECT 
        trip_uuid, 
        action_center,
        MAX(trip_time) as mts_trip_depart_time
    FROM base_trips
    WHERE action_performed = 'Apply NSL' 
      AND nsl = 'DP-LF-01'
    GROUP BY 1,2
),

load_info AS (
    SELECT 
        trip_uuid, 
        action_center,
        MAX(trip_time) as last_shipment_load_time
    FROM base_trips
    WHERE action_performed = 'Loading' 
    GROUP BY 1,2
),

prime_arrival_time as (
    select trip_uuid,route_type, vehicle_type,
 -- vehicle_type_sec, vehicle_number, vehicle_number_sec,
 min(trip_time) as prime_vehicle_arrival_time 
FROM base_trips
where ((vehicle_number_sec is not null) and (trim(vehicle_number_sec) <> ''))  
group by 1, 2, 3
)

,trip_complete_time_data_2 as (
    select trip_uuid, vehicle_number,
 max(trip_time) as trip_complete_time 
FROM base_trips
where action_performed = 'Completed'  
group by 1, 2
)

,trip_complete_time_data as 
(select route_schedule_uuid, trip_uuid,
 vehicle_type, vehicle_number, vehicle_number_sec_filled,
  COALESCE(NULLIF(trim(vehicle_number_sec_filled), ''), vehicle_number) as priority_vehicle_num,
  trip_time as trip_complete_time
from 
(select distinct route_schedule_uuid, route_type, vehicle_type, vehicle_type_sec,
vehicle_number,vehicle_number_sec,
MAX_BY(vehicle_number_sec,CASE WHEN vehicle_number_sec IS NULL THEN NULL ELSE action_date END
) OVER (PARTITION BY trip_uuid ORDER BY action_date) as vehicle_number_sec_filled,
    trip_uuid,next_transit_center, action_performed, action_center, 
from_unixtime( action_date/1000000.0) + interval '330' minute trip_time, action_date
FROM base_trips
where  action_performed in ('Arrived','Completed')
)
where action_performed in ('Completed') )


--  Join all tables together
SELECT 
    a.route_schedule_uuid, 
    a.trip_uuid,
    a.route_type,  
    a.action_center as current_center_id,
    b.property_facility_name as center_name, 
    a.position as center_position,
    c.property_facility_name as next_center_name, 
    a.scheduled_arrival_time, 
    d.scheduled_depart_time,
    p.prime_vehicle_arrival_time,
    a.trip_arrival_time, 
    l.last_shipment_load_time, 
    d.trip_depart_time,
    m.mts_trip_depart_time,
    t.vehicle_number_sec_filled,
    t.priority_vehicle_num,
    t.trip_complete_time
FROM arrival_info a
-- Join specific events to the arrival event based on Trip + Center
LEFT JOIN depart_info d 
    ON a.trip_uuid = d.trip_uuid 
    AND a.action_center = d.action_center
LEFT JOIN mts_info m 
    ON a.trip_uuid = m.trip_uuid 
    AND a.action_center = m.action_center
LEFT JOIN load_info l 
    ON a.trip_uuid = l.trip_uuid 
    AND a.action_center = l.action_center
LEFT JOIN prime_arrival_time p
    ON a.trip_uuid = p.trip_uuid
LEFT JOIN trip_complete_time_data t
    ON a.trip_uuid = t.trip_uuid
-- Join Facility Names
LEFT JOIN hudi_db.hudi_facility_parquet b 
    ON a.action_center = b.property_facility_facility_code
LEFT JOIN hudi_db.hudi_facility_parquet c 
    ON a.next_transit_center = c.property_facility_facility_code

where a.next_transit_center is not null

'''

In [0]:
cur = conn.cursor()
cur.execute(trips_arrive_depart_query)
columns = [desc[0] for desc in cur.description]
data = cur.fetchall()
trips_arrive_depart_df = pd.DataFrame(data, columns=columns)
cur.close()
conn.close()

In [0]:
trips_arrive_depart_df_spark  = spark.createDataFrame(trips_arrive_depart_df)

In [0]:
# display(trips_arrive_depart_df_spark)
# display(trip_route_data_joined.filter((col('trip_uuid').isin('trip-176127834828421218'))))

# display(trips_arrive_depart_df_spark.filter(col('trip_uuid')=='trip-176358634779354166'))

route_schedule_uuid trip_uuid route_type current_center_id center_name center_position next_center_name scheduled_arrival_time scheduled_depart_time prime_vehicle_arrival_time trip_arrival_time last_shipment_load_time trip_depart_time mts_trip_depart_time vehicle_number_sec_filled priority_vechicle_num trip_complete_time thanos::sroute:6a346ad0-4988-4a8d-a5d6-2f1a26ee266d trip-176413770231551603 ADHOC IN122103A1J North_Store 0 Gurgaon_Tauru_GW 2025-11-26 09:00:00.000 2025-11-26 09:00:00.000 null 2025-11-26 11:45:02.400 UTC 2025-11-26 14:01:38.300 UTC 2025-11-26 14:58:16.300 UTC 2025-11-26 15:22:52.000 UTC null UK17CA6274 2025-11-27 10:51:01.400 UTC thanos::sroute:d6170ce7-5b10-4e2d-ba44-b5d490ff5085 trip-176350995762826343 CARTING INDLAXET Delhi_Pitampura2_D 1 Delhi_UdhyogNgr_I 2025-11-19 06:45:00.000 2025-11-19 07:15:00.000 null 2025-11-19 07:00:03.600 UTC 2025-11-19 07:04:28.800 UTC 2025-11-19 07:08:18.700 UTC null null DL01LAL0233 2025-11-19 08:42:45.700 UTC thanos::sroute:9590bda8-5e63-444c-ac3b-eeba53717c6a trip-176327417417889997 CARTING INMHAWJE Mumbai_Mirabhayandar_I 0 Mumbai_Uttan_D 2025-11-16 12:30:00.000 2025-11-16 12:30:00.000 null 2025-11-16 11:52:54.200 UTC 2025-11-16 11:53:22.200 UTC 2025-11-16 12:02:54.000 UTC 2025-11-16 12:09:22.000 UTC null MH04KF9892 2025-11-16 14:16:36.100 UTC thanos::sroute:c234bbdc-e9cb-4202-9d21-1999b99f8f7a trip-176314107997592658 FTL INKLAAII Kollam_Kilikollur_H 0 Bangalore_Hoskote_GW 2025-11-15 03:30:00.000 2025-11-15 07:00:00.000 2025-11-14 22:54:03.200 UTC 2025-11-14 22:54:40.000 UTC 2025-11-15 05:18:53.000 UTC 2025-11-15 05:58:32.500 UTC 2025-11-15 06:12:58.000 UTC KA51AH6368 KA51AH6368 2025-11-16 07:49:48.900 UTC thanos::sroute:5ec43a11-2847-49ae-a666-35aa63a544f7 trip-176344107142156264 CARTING INHRBBSJ Faridabad_PadamNagar_D 1 Faridabad_MathuraRoad_GW 2025-11-18 13:30:00.000 2025-11-18 13:45:00.000 null 2025-11-18 13:00:06.500 UTC 2025-11-18 13:32:53.800 UTC 2025-11-18 13:34:28.500 UTC 2025-11-18 13:35:59.000 UTC null HR55AX7023 2025-11-18 14:09:16.600 UTC thanos::sroute:6fc0de5f-b7da-4d26-a6a6-7281aeda098c trip-176254945484331475 CARTING IN465001A1B Shajapur_Mahupura_D 2 PolayKalan_Himmatpura_DPP 2025-11-08 07:15:00.000 2025-11-08 07:45:00.000 null 2025-11-08 07:11:52.800 UTC 2025-11-08 08:07:40.900 UTC 2025-11-08 08:10:46.000 UTC 2025-11-08 08:14:32.000 UTC MP41ZJ8246 2025-11-08 14:58:38.000 UTC thanos::sroute:ae9cd615-1ca8-4fb3-bb21-4fa26f2cb385 trip-176387990282546476 AIR IN560300A1D Bengaluru_KGAirprt_OT 0 Nagpur_Gondkhry_DT 2025-11-23 13:30:00.000 2025-11-23 13:30:00.000 null 2025-11-23 12:08:22.800 UTC null 2025-11-23 15:33:52.700 UTC null null 6E 6891 2025-11-23 19:44:32.800 UTC thanos::sroute:af7bcc22-f753-4f64-9ff8-e34fef04f2e8 trip-176415068674830271 CARTING INHRBBVQ Gurgaon_Pathradi_H 0 Gurgaon_Bhorakalan_R 2025-11-26 22:00:00.000 2025-11-26 22:00:00.000 null 2025-11-26 15:21:26.800 UTC 2025-11-26 19:53:48.200 UTC 2025-11-26 20:16:48.200 UTC 2025-11-26 20:41:08.000 UTC null HR38AC2649 2025-11-27 01:30:48.000 UTC thanos::sroute:30cd5e95-a9db-426f-bf5b-9d5ca6883a41 trip-176294726355073168 CARTING INDLBDXT Delhi_Naraina_L 0 Gurgaon_Tauru_GW 2025-11-13 02:00:00.000 2025-11-13 02:00:00.000 null 2025-11-12 17:04:23.600 UTC 2025-11-13 01:51:44.500 UTC 2025-11-13 01:53:37.100 UTC 2025-11-13 02:49:49.000 UTC null DL01MA8416 2025-11-13 07:11:34.800 UTC thanos::sroute:14bae0ce-fe33-47e0-aad6-a4f9847751e6 trip-17628119021078970 CARTING INWBAYMZ Dinhata_WardNo6_D 1 Sitai_Khamarsitai_DPP 2025-11-11 06:30:00.000 2025-11-11 07:00:00.000 null 2025-11-11 06:47:26.600 UTC 2025-11-11 07:47:19.400 UTC 2025-11-11 07:52:58.500 UTC 2025-11-11 07:53:34.000 UTC null WB73F9381 2025-11-11 16:38:31.500 UTC thanos::sroute:b58410e1-1d15-48a9-bebf-d7d20f77ee5f trip-176283665583504528 CARTING INMHAPVP Bhiwandi_Lonad_GW 0 Mumbai_CharkopIndEstate_L 2025-11-11 11:00:00.000 2025-11-11 11:00:00.000 null 2025-11-11 10:20:55.800 UTC 2025-11-11 12:54:58.700 UTC 2025-11-11 12:57:58.500 UTC 2025-11-11 13:45:4

In [0]:
from pyspark.sql.functions import to_timestamp, unix_timestamp, abs, date_format, to_date

trip_route_data_joined = trips_arrive_depart_df_spark.join(route_id_route_set_mapping_spark, 'route_schedule_uuid', 'left')

trip_route_data_joined = (trip_route_data_joined
                          .withColumn('route_set_id', when(col('route_set_id').isNull(),col('route_schedule_uuid')).otherwise(col('route_set_id')))
                          .withColumn("last_shipment_load_time",to_timestamp("last_shipment_load_time", "yyyy-MM-dd HH:mm:ss.SSS z"))
                              .withColumn("trip_depart_time",to_timestamp("trip_depart_time", "yyyy-MM-dd HH:mm:ss.SSS z"))
                              .withColumn("prime_vehicle_arrival_time",to_timestamp("prime_vehicle_arrival_time", "yyyy-MM-dd HH:mm:ss.SSS z"))
                              .withColumn("trip_arrival_time",to_timestamp("trip_arrival_time", "yyyy-MM-dd HH:mm:ss.SSS z"))
                              .withColumn("mts_trip_depart_time",to_timestamp("mts_trip_depart_time", "yyyy-MM-dd HH:mm:ss.SSS z"))
                              .withColumn("trip_complete_time",to_timestamp("trip_complete_time", "yyyy-MM-dd HH:mm:ss.SSS z"))
                              .withColumn("scheduled_depart_time",to_timestamp("scheduled_depart_time", "yyyy-MM-dd HH:mm:ss.SSS"))
                              .withColumn("scheduled_arrival_time",to_timestamp("scheduled_arrival_time", "yyyy-MM-dd HH:mm:ss.SSS"))
                              .withColumn("scheduled_depart_day",to_date("scheduled_depart_time"))
                              .withColumn("arrival_diff_hours", (col("trip_arrival_time").cast("long") - col("scheduled_arrival_time").cast("long")) / 3600.0)
                              .withColumn("prime_arrival_sch_depart_diff_hours", (col("prime_vehicle_arrival_time").cast("long") - col("scheduled_depart_time").cast("long")) / 3600.0)
                              .withColumn("last_shipment_scheduled_depart_diff_hours", (col("last_shipment_load_time").cast("long") - col("scheduled_depart_time").cast("long")) / 3600.0)
                              .withColumn("depart_diff_hours", (col("trip_depart_time").cast("long") - col("scheduled_depart_time").cast("long")) / 3600.0)
                              .withColumn("mts_depart_diff_hours", (col("mts_trip_depart_time").cast("long") - col("scheduled_depart_time").cast("long")) / 3600.0)
                              .withColumn("obsl_delay", when((col("depart_diff_hours") > 0) | (col("mts_depart_diff_hours") > 1) , lit(1)).otherwise(lit(0)))
                              )


# display(trip_route_data_joined)

In [0]:
# display(trip_route_data_joined.filter(col('route_set_id').isNull()))

In [0]:
# center_name = 'Pune_Chimbali_H'
# date = '2025-11-22'
# display(trip_route_data_joined.filter(
#      (col('scheduled_depart_day')==date)&
#     (col('center_name')==center_name)&(col('route_type')=='FTL')
#         &(col('obsl_delay')==1)
#         ))
#         # .groupBy('scheduled_depart_day','center_name','route_type','obsl_delay').agg(count('*').alias('count')))

In [0]:
# delay_trips_df = trip_route_data_joined.filter((col('obsl_delay')==1))
# display(delay_trips_df)


In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import rank 

w = Window.partitionBy("trip_uuid").orderBy("scheduled_arrival_time")
vehicle = Window.partitionBy("route_set_id","priority_vehicle_num").orderBy("trip_complete_time")
vehicle_2 = Window.partitionBy("route_set_id","priority_vehicle_num","center_position").orderBy("trip_complete_time")


base_cond = (
    (col("center_position") == 0) &
    (col("delay_arrive_delay_depart") == 1) &
    (col("delay_arrive_delay_depart_last_center") == 1) &
    (col("last_trip_current_report_time_diff_hours") > 0) 
    
)
# & (col("last_2_trip_last_report_time_diff_hours") > 0)

trip_route_data_joined = (trip_route_data_joined.withColumn("prev_arrival_diff_hours", lag("arrival_diff_hours").over(w))
                        #   .withColumn("center_position", rank().over(w))
                          .withColumn("vehicle_route_last_1_complete_time", lag("trip_complete_time").over(vehicle_2))
                          .withColumn("vehicle_route_last_1_trip_id", lag("trip_uuid").over(vehicle_2))
                          .withColumn("vehicle_route_last_2_complete_time", lag("trip_complete_time",2).over(vehicle_2))
                          .withColumn("vehicle_route_last_2_trip_id", lag("trip_uuid",2).over(vehicle_2))
                          .withColumn("vehicle_route_last_1_sch_arrival_time", lag("scheduled_arrival_time").over(vehicle_2))
                          .withColumn("last_trip_current_report_time_diff_hours", (col("vehicle_route_last_1_complete_time").cast("long") - col("scheduled_arrival_time").cast("long")) / 3600.0)
                          .withColumn("last_2_trip_last_report_time_diff_hours", (col("vehicle_route_last_2_complete_time").cast("long") - col("vehicle_route_last_1_sch_arrival_time").cast("long")) / 3600.0)
                          .withColumn('delay_arrive_delay_depart',when((col("arrival_diff_hours") > 0) & 
                         (col("depart_diff_hours")>1),lit(1)).otherwise(lit(0)))
                           .withColumn("delay_arrive_delay_depart_last_center", lag("delay_arrive_delay_depart").over(vehicle_2))
                           .withColumn("delay_arrive_delay_depart_last_2_center", lag("delay_arrive_delay_depart",2).over(vehicle_2))
                        # .withColumn("rotation_issue",
                        #             when(((col("center_position")==0) &
                        #                    (col('delay_arrive_delay_depart')==1)& 
                        #                    (col('delay_arrive_delay_depart_last_center')==1)&
                        #                     (col('last_trip_current_report_time_diff_hours')>0)& 
                        #                     (col('last_2_trip_last_report_time_diff_hours')>0)),lit(1)).otherwise(lit(0)))
                        
                        .withColumn(  "rotation_issue", when(base_cond & (col("delay_arrive_delay_depart_last_2_center") > 0), lit(2))
                         .when(base_cond, lit(1)).otherwise(lit(0)))
                        
                            # .drop('prev_arrival_diff_hours')
                                        )

In [0]:
# display(trip_route_data_joined.filter(
#     (col('rotation_issue')>=1)
#     & (col('scheduled_depart_day')>='2025-11-18')
#     # & (col('center_name')==center_name)
#     # & (col('center_position')==1)
#     # &(col('route_type')!='AIR')
#         # &(col('obsl_delay')==1)
#     )
#         )

In [0]:
# route_set_id = 'thanos::routeset:7d6623f5-cfd9-43ef-8f27-5933d9a8e036'
# priority_vehicle_num = 'MH04KU0042'

# display(trip_route_data_joined.filter((col('route_set_id')==route_set_id)&(col('priority_vehicle_num')==priority_vehicle_num)&(col('center_position')==0)).select('route_set_id','route_schedule_uuid',
#  'trip_uuid',
#  'route_type',
#  'center_name','center_position',
#  'scheduled_arrival_time',
#  'scheduled_depart_time',
#  'priority_vehicle_num',
#  'vehicle_route_last_1_trip_id',
#  'vehicle_route_last_2_trip_id',
#  'scheduled_depart_day',
#  'rotation_issue',
#  'obsl_delay'))        

In [0]:
from pyspark.sql.functions import current_date

rotation_issues = trip_route_data_joined.filter(
    (col('rotation_issue')>=1)
    & (col('scheduled_depart_day')>=data_analysis_date)).withColumn('ad',current_date()).withColumn('center_position',col('center_position').cast('int')).select('route_set_id','route_schedule_uuid','trip_uuid', 'route_type', 'center_name','center_position', 'scheduled_arrival_time', 'scheduled_depart_time', 'priority_vehicle_num', 'vehicle_route_last_1_trip_id','vehicle_route_last_2_trip_id', 'scheduled_depart_day', 'rotation_issue','obsl_delay','ad')

display(rotation_issues)
        

route_set_id route_schedule_uuid trip_uuid route_type center_name center_position scheduled_arrival_time scheduled_depart_time priority_vechicle_num vehicle_route_last_1_trip_id vehicle_route_last_2_trip_id scheduled_depart_day rotation_issue obsl_delay thanos::routeset:393aa066-893b-42b5-9db3-5bc4cb73f901 thanos::sroute:6c5703c3-aa03-4c7f-9f89-05314629c8cb trip-176335245821705594 AIR Patna_OT 0 2025-11-17T08:30:00Z 2025-11-17T08:30:00Z 6E 805 trip-176326642190801862 trip-176318000931590224 2025-11-17 2 1 thanos::routeset:393aa066-893b-42b5-9db3-5bc4cb73f901 thanos::sroute:6c5703c3-aa03-4c7f-9f89-05314629c8cb trip-176404361573852412 AIR Patna_OT 0 2025-11-25T08:30:00Z 2025-11-25T08:30:00Z 6E 805 trip-176395788707972924 trip-176387083151770743 2025-11-25 2 1 thanos::routeset:393aa066-893b-42b5-9db3-5bc4cb73f901 thanos::sroute:6c5703c3-aa03-4c7f-9f89-05314629c8cb trip-176395788707972924 AIR Patna_OT 0 2025-11-24T08:30:00Z 2025-11-24T08:30:00Z 6E 805 trip-176404361573852412 trip-176395788707972924 2025-11-24 2 1 thanos::routeset:6e2db925-efa9-41e4-89c3-4180cb4b23cf thanos::sroute:c498b053-e684-4e12-96ab-7b0bf8052996 trip-176362266501223305 ADHOC Meerut_Temp_R 0 2025-11-20T09:00:00Z 2025-11-20T09:00:00Z UP78GT8061 trip-176361322226263172 null 2025-11-20 1 1 thanos::routeset:80222223-eaa8-4e1a-b784-903a5579768c thanos::sroute:60cdf3cf-4ca3-459d-8bda-b0a796eea3bb trip-176377945213084684 CARTING Singrauli_Waidhan2_D 0 2025-11-21T21:00:00Z 2025-11-21T21:00:00Z HR38AD6303 trip-176369133015854218 trip-176369103513187169 2025-11-21 1 1 thanos::routeset:80222223-eaa8-4e1a-b784-903a5579768c thanos::sroute:60cdf3cf-4ca3-459d-8bda-b0a796eea3bb trip-176386583838784340 CARTING Singrauli_Waidhan2_D 0 2025-11-22T21:00:00Z 2025-11-22T21:00:00Z HR38AD6303 trip-176377945213084684 trip-176369133015854218 2025-11-22 2 1 thanos::routeset:982cc827-ae21-41c1-a16b-132be03d8862 thanos::sroute:9dc7e3ae-13e5-448a-9785-9854e1bde0c3 trip-176336730792241933 FTL Leh_Skarayokma_DPP 0 2025-11-17T07:00:00Z 2025-11-17T07:30:00Z JK10A8215 trip-176327793920723629 trip-176319628764653434 2025-11-17 2 1 thanos::routeset:982cc827-ae21-41c1-a16b-132be03d8862 thanos::sroute:9dc7e3ae-13e5-448a-9785-9854e1bde0c3 trip-176345375172950378 FTL Leh_Skarayokma_DPP 0 2025-11-18T07:00:00Z 2025-11-18T07:30:00Z JK10A8215 trip-176336730792241933 trip-176327793920723629 2025-11-18 2 1 thanos::routeset:982cc827-ae21-41c1-a16b-132be03d8862 thanos::sroute:9dc7e3ae-13e5-448a-9785-9854e1bde0c3 trip-176353967722739351 FTL Leh_Skarayokma_DPP 0 2025-11-19T07:00:00Z 2025-11-19T07:30:00Z JK10A8215 trip-176345375172950378 trip-176336730792241933 2025-11-19 2 1 thanos::routeset:a9b4b573-0150-4ee5-acc7-e9305b7308ca thanos::sroute:ccb73a14-878d-4e3a-a802-4a8be5e745d3 trip-176366930982190833 AIR Mumbai_OT 0 2025-11-21T01:15:00Z 2025-11-21T01:15:00Z 6E 534 trip-176358171842385292 trip-176358171481084749 2025-11-21 1 1 thanos::routeset:eb610a05-9648-4492-acd2-cebd2714b3a9 thanos::sroute:a945cc04-e86f-49ae-8f15-5af2411f4301 trip-176402151046000244 AIR Delhi_Airport_OT 0 2025-11-25T03:00:00Z 2025-11-25T03:00:00Z 6E 2993 trip-176393593287814868 trip-176358006857290132 2025-11-25 1 1 thanos::routeset:0aa489d6-532e-42ba-b988-358d0292ab72 thanos::sroute:749dfff7-031b-4777-b67a-6debc0fa5567 trip-176389386459224337 AIR Mumbai_OT 0 2025-11-23T16:00:00Z 2025-11-23T16:00:00Z QP 1120 trip-176380863503225596 trip-176371913154545824 2025-11-23 1 1 thanos::routeset:0aa489d6-532e-42ba-b988-358d0292ab72 thanos::sroute:749dfff7-031b-4777-b67a-6debc0fa5567 trip-176380863503225596 AIR Mumbai_OT 0 2025-11-22T16:00:00Z 2025-11-22T16:00:00Z QP 1120 trip-176389386459224337 trip-176380863503225596 2025-11-22 2 1 thanos::routeset:33451f23-a64c-49d1-a1cf-d214d72ee236 thanos::sroute:d1924d36-9609-47da-8a26-5d9a6af1913f trip-176339322565978555 FTL Sambalpur_Tentelpara_H 0 2025-11-17T18:00:00Z 2025-11-17T20:30:00Z RJ14GR8860 trip-176334288144838518 trip-176330354694059340 2025-11-17 1 1 thanos::routeset:33451f23-a64c-49d1-a1cf-d214

In [0]:
# display(trip_route_data_joined.filter(col('trip_uuid')=='trip-176376353031603276'))
# display(trip_route_data_joined.filter(col('vehicle_number')=='HR55AG0187'))

In [0]:

# ##### Loading complete by scheduled depart time
# trip_route_data_joined = (trip_route_data_joined.withColumn("Loading_not_complete_by_schedule_depart",
#                                  when(col('last_shipment_scheduled_depart_diff_hours')>0,lit(1)).otherwise(lit(0))))


# ##### prime delay time
# trip_route_data_joined = trip_route_data_joined.withColumn('Prime_placement_Delay', when((col("prime_arrival_sch_depart_diff_hours") > 0) & (col("center_position")==1),lit(1)).otherwise(lit(0)))


# #### Geofence issue
# trip_route_data_joined = trip_route_data_joined.withColumn('geofence_issue', when((col("depart_diff_hours") <= 0) & (col("mts_depart_diff_hours")>1),lit(1)).otherwise(lit(0)))

In [0]:
# display(trip_route_data_joined.filter((col('trip_uuid').isin('trip-176377863352885867'))))
# display(trip_route_data_joined.filter((col('geofence_issue')==1)))


In [0]:
# display(trip_route_data_joined.filter((col('trip_uuid')=='trip-176354659485612192')))

In [0]:
# dbutils.fs.rm('s3://abis3/Sheetal/trip_obsl_data/rotation_issues_trips_list', True)

In [0]:
rotation_issues_path = "s3://abis3/Sheetal/trip_obsl_data/rotation_issues_trips_list"
# .coalesce(1)
# (rotation_issues.write.mode("append").option("header", True)
#     .option("quote", '"')          
#     .option("escape", '"')  
#     .option("multiLine", True)
#     .partitionBy("ad")    
#     .csv(rotation_issues_path))

rotation_issues.write.mode("append").partitionBy("ad").parquet(rotation_issues_path) 

print(rotation_issues_path)

s3://abis3/Sheetal/trip_obsl_data/rotation_issues_trips_list


In [0]:
### Delete file from s3 bucket
# dbutils.fs.rm('s3://abis3/Sheetal/trip_obsl_data/rotation_issues_trips_list.csv', True)

True